In [1]:
from PyRuSH.RuSH import RuSH
from pyConTextNLP import pyConTextGraph
from DocumentClassifier import DocumentClassifier 
from pyConTextNLP.utils import get_document_markups

from DocumentClassifier import FeatureInferencer
from DocumentClassifier import DocumentInferencer
from nlp_pneumonia_utils import markup_sentence
from itemData import get_item_data
from visual import convertMarkups2DF


# begin to define MyPipe class
class MyPipe:
    def __init__(self, sentence_rules, target_rules, context_rules, feature_inference_rule, document_inference_rule):
        # initiate necessary components here        
        self.sentence_segmenter = RuSH(sentence_rules)
        self.targets=get_item_data(target_rules)
        self.modifiers=get_item_data(context_rules)
        self.feature_inferencer=FeatureInferencer(feature_inference_rule)
        self.document_inferencer = DocumentInferencer(document_inference_rule)
    
    def process(self, doc_text):        
        #process your input doc_text, return the required results
        sentences=self.sentence_segmenter.segToSentenceSpans(doc_text)
        #sentences=doc_text.split('\n')
        context_doc = pyConTextGraph.ConTextDocument()

        for sentence in sentences:
            sentence_text=doc_text[sentence.begin:sentence.end].lower()
            print(sentence_text)
            # Process every sentence by adding markup
            m = markup_sentence(sentence_text, modifiers=self.modifiers, targets=self.targets)
            context_doc.addMarkup(m)
            #context_doc.getSectionMarkups()
        
        markups = get_document_markups(context_doc)
        annotations, relations, doc_txt = convertMarkups2DF(markups) 
        
        inferenced_types = self.feature_inferencer.process(annotations, relations)
        doc_class = self.document_inferencer.process(inferenced_types)
        
        return doc_class, context_doc, annotations, relations

In [2]:
# configure your rules 

sentence_rules='rush_rules.tsv'
# you can point target_rules to a file path instead, if there are many rules
target_rules='target_rules.yml'
context_rules='context_rules.yml'
feature_inference_rule='''
#Conclusion type, Evidence type, Modifier values associated with the evidence
NEGATED_CONCEPT,FBI,DEFINITE_NEGATED_EXISTENCE
'''
# define the document inference rule
document_inference_rule='''
#Conclusion Type at document level, Evidence type at mention level
FBI_DOC,FBI
RATS_DOC,RATS
ROACH_DOC,ROACH

#Default document type
NO_FINDINGS
'''

In [3]:
#initiate an instance of MyPipe
myPipe=MyPipe(sentence_rules, target_rules, context_rules, feature_inference_rule, document_inference_rule)

In [4]:
document = "There was a cockroach and mouse that made me epi sick"
result = myPipe.process(document)
print(result)

there was a cockroach and mouse that made me epi sick
('fbi_doc', __________________________________________
,   markup_id vis_category start end        txt   type
0        T0       Target    12  21  cockroach  roach
1        T1       Target    45  48        epi    fbi
2        T2       Target    26  31      mouse   rats, Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])


In [5]:
#import pymysql
import pandas as pd
#import getpass

In [6]:
food_data = pd.read_csv('Complaints_training.csv', delimiter = ",", index_col = "Request Number")

#food_data = food_data["Request Number","Conditions"]
food_data["Conditions"]
#food_data.index.values

Request Number
77011     COMPLAINANT STATES THAT CAFETERIA MANAGER DOES...
94933     No employees have food handler permits, no hot...
123727    The store has numerous mice and rats that I ha...
63356     DON'T HAVE FOOD HANDLER CARDS, GLOVE ARE NOT B...
148793    Date of Occurrence: 11/19/2017.  Time of order...
123871    Very dirty toilet and toilet rooms. No hand so...
98695     No one in the restaurant was handling food pro...
118305    There was a long strand of hair in the hamburg...
51306     CUSTOMERS AND EMPLOYEES ARE SMOKING INSIDE THI...
92761     Customer ordered a hamburger, the hamburger wa...
93892     Found 1/2 inch bolt and a staple in the chow m...
50463     EMPLOYEE CUT FINGER WHILE MAKING SANDWICH FOR ...
42890                   ROACH IN FOOD (SHRIMP DIABLO PASTA)
84384     Chicken strips were served frozen. Patron touc...
72204     CUSTOMER SAW A COUPLE OF MICE RUNNING AROUND I...
103936    Ordered the vegetable soup and as she at to th...
103903    Employee vomite

In [7]:
#print(food_data.Conditions)
food_data1 = food_data.transpose()
#print(food_data1)
#food_data1.describe()

In [ ]:
# write you code here, fill the results by processing each document through MyPipe
results=dict()  # this dictionary will contain document names as keys and result as values.
for index, row in food_data1.iteritems():
    try:
        t = str(row[13]).replace('\n',' ')
        #print(t)
        result = myPipe.process(t)
        results[index] = result
    except:
        continue
    print(result)


complainant states that cafeteria manager does not wash their hands at appropriate times when preparing foods. complainant also states that old stained wash cloths are used to clean off food prep surfaces. finally, complainant states that the cafeteria manager sticks their fingers in foods to taste them and that the manager was observed coughing above some tater tots yesterday.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
no employees have food handler permits, no hot water, no soap and re-using food- multiple reheating and cooling.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
the store has numerous

bare hand contact - teachers handle food.  food sits out for prolonged periods.  complainant had a child enrolled for 5 months.  child had a stomach ailment every week.  complainant pulled child out and child has stopped having stomach ailments.
('fbi_doc', __________________________________________
,   markup_id vis_category start  end      txt type
0        T0       Target   138  145  stomach  fbi
1        T1       Target   224  231  stomach  fbi, Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
mold everywhere.
serving expired products.
serving food out of temperature.
sick employees working.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
suspected food borne illness
('no_findings', __________________________________________
, Empty DataFrame
Co

Index: [])
mice poop in rice and whatever else.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
employees are not wearing gloves.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
unclean environment; barehand contact; ceiling in disrepair; prep food in dish wash area
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
has food out, most of it uncovered.
('no_findings', __________________________________________
, Empty 

('fbi_doc', __________________________________________
,   markup_id vis_category start end     txt type
0        T0       Target    33  39  nausea  fbi
1        T1       Target    56  61   fever  fbi, Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
imporoperly identified and stored meat products
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
leave garbage bins open at all times and there is a bad smell coming from them.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
a salad was served with a tomato wedge that had worm holes and a worm inside of the tomato

employees of the taco cart on the corner of 800 s & main in front of western wholesale flooring frequently urinate on the building & parking lot.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
cockroaches were present in the establishment, food area was dirty.
date off occurrence 8/29 during the afternoon
('roach_doc', __________________________________________
,   markup_id vis_category start end        txt   type
0        T0       Target     0   9  cockroach  roach, Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
saw a mouse in the center aisle.
('rats_doc', __________________________________________
,   markup_id vis_category start end    txt  type
0        T0       Target     6  11  mouse  rats, Empty DataFrame
Columns: [relation_id, type, arg

...

('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
date occurred: 4/4/17  time: 11:00am employees go to break with apron on and take it to bathroom and it touches the floor.
put hairnet on and doesn't wash hands afterwards.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
mold on the walls, missing caulking and poor conditions in bathroom.
general condition of repair and sanitation overall is very poor.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id

('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
the coffee bar is filthy.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
dirty didn't clean the tables no one washed their hands.
none of the cooks had hair nets on.
no soap in the woman's bathroom
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
the drink machine is draining into a bucket and over flowing and leaking through ceiling tiles.
('no_findings', ___________

date occurred: 06/08/12 time occurred: 7:30pm accepted money for an ice cream cone and then took the cone and filled it with ice cream and handed it to her without washing his hands first.
when she complained they told her that no one has ever told them they couldn't do it that way.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
dirty water glasses were provided to customers. customer suspects that an omelet served to her husband was re-served to a differed customer before he could eat it.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
disgusting build up of grease on the fryers.  foreign object was fou

while waiting for coffee to be brewed customer observed 2 cockroaches on the serving counter top.
customer informed the manager and he asked customer if he knew where they had come from.
manager picked up the cockroach with a napkin and tossed it.
did not observe manager wash his hands.
('roach_doc', __________________________________________
,   markup_id vis_category start  end        txt   type
0        T0       Target    58   67  cockroach  roach
1        T1       Target   120  129  cockroach  roach, Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
temp log is not accurate, employees just record temperature w/out physically temp, do not wear gloves and wash their hands frequently, not rotating products specially meat and chicken, eating on the line, the kitchen is so filthy, old grease underneath the grill, the floor, no thermometer in the cooler and freezer,, i was employed there more than 3 weeks as a part time line cook but i juts q

the dishes are dirty at the buffet line.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
fbi report.
('fbi_doc', __________________________________________
,   markup_id vis_category start end  txt type
0        T0       Target     0   3  fbi  fbi, Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
store is filthy.
the health permit is expired on the wall.
dried, crusted food on the make line.
rotten food in the walk in.
('no_findings', __________________________________________
, Empty DataFrame
Columns: [markup_id, vis_category, start, end, txt, type]
Index: [], Empty DataFrame
Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
Index: [])
employee became ill and was vomiting at work.  the manager, spencer davidson, insisted that th

In [9]:
results

{77011: ('no_findings',
  __________________________________________,
  Empty DataFrame
  Columns: [markup_id, vis_category, start, end, txt, type]
  Index: [],
  Empty DataFrame
  Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
  Index: []),
 94933: ('no_findings',
  __________________________________________,
  Empty DataFrame
  Columns: [markup_id, vis_category, start, end, txt, type]
  Index: [],
  Empty DataFrame
  Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
  Index: []),
 123727: ('no_findings',
  __________________________________________,
  Empty DataFrame
  Columns: [markup_id, vis_category, start, end, txt, type]
  Index: [],
  Empty DataFrame
  Columns: [relation_id, type, arg1_cate, arg1_id, arg2_cate, arg2_id]
  Index: []),
 63356: ('no_findings',
  __________________________________________,
  Empty DataFrame
  Columns: [markup_id, vis_category, start, end, txt, type]
  Index: [],
  Empty DataFrame
  Columns: [relation_id, typ

In [10]:
results_export = pd.DataFrame.from_dict(results)
results_export_full = results_export
results_export_full = results_export_full.T
results_export_full.columns = ['Request Number', 'Findings', 'Category', 'Relationships']
results_export = results_export.iloc[0]
results_export.to_csv('Original_data.csv', ",")
results_to_chunk = pd.DataFrame.from_dict(results)
#print(results_export)
for index, row in results_export_full.iteritems():
    try:
        p = results_export_full[results_export_full['Request Number'].str.contains("rats")]
        q = results_export_full[results_export_full['Request Number'].str.contains("roach")]
        f = results_export_full[results_export_full['Request Number'].str.contains("fbi")]
    except:
        continue
only_pests = pd.concat([p, q])
all_positive = pd.concat([p,q,f])
print(all_positive)
print(only_pests)
only_pests.to_csv('Only_pests.csv', ",")
all_positive.to_csv('All_positive.csv', ",")
    

       Request Number                                      Findings  \
45750        rats_doc  __________________________________________\n   
46144        rats_doc  __________________________________________\n   
46758        rats_doc  __________________________________________\n   
46760        rats_doc  __________________________________________\n   
46773        rats_doc  __________________________________________\n   
47018        rats_doc  __________________________________________\n   
47509        rats_doc  __________________________________________\n   
47601        rats_doc  __________________________________________\n   
52349        rats_doc  __________________________________________\n   
52801        rats_doc  __________________________________________\n   
53310        rats_doc  __________________________________________\n   
56383        rats_doc  __________________________________________\n   
56768        rats_doc  __________________________________________\n   
56851 

       Request Number                                      Findings  \
45750        rats_doc  __________________________________________\n   
46144        rats_doc  __________________________________________\n   
46758        rats_doc  __________________________________________\n   
46760        rats_doc  __________________________________________\n   
46773        rats_doc  __________________________________________\n   
47018        rats_doc  __________________________________________\n   
47509        rats_doc  __________________________________________\n   
47601        rats_doc  __________________________________________\n   
52349        rats_doc  __________________________________________\n   
52801        rats_doc  __________________________________________\n   
53310        rats_doc  __________________________________________\n   
56383        rats_doc  __________________________________________\n   
56768        rats_doc  __________________________________________\n   
56851 

In [11]:
from visual import view_pycontext_output
from visual import view_pycontext_outputs
from visual import Vis

In [12]:
#get the context documents that you created in Exercise 2 and put them into a dictionary.
context_docs=dict()
i=0
for item, row in results.items(): 
    doc_name = "doc" + str(i)
    context_docs[doc_name]=row[1]
    i=i+1

In [13]:
view_pycontext_output(context_docs['doc1'], Vis(file_name="test.html"))

In [14]:
view_pycontext_outputs(context_docs)

A Jupyter Widget

In [21]:
#match up indexes from findings with indexes from the test data to return zipcodes.
import itertools
zipcodes = food_data.index.intersection(all_positive.index)
all_zips = (food_data.loc[zipcodes])
#all_zips["PR ZIP"]
pzipcodes = food_data.index.intersection(p.index)
rats_zips = (food_data.loc[pzipcodes])
#print(rats_zips["PR ZIP"])
qzipcodes = food_data.index.intersection(q.index)
roach_zips = (food_data.loc[qzipcodes])
#print(roach_zips["PR ZIP"])
fzipcodes = food_data.index.intersection(f.index)
fbi_zips = (food_data.loc[fzipcodes])
#print(fbi_zips["PR ZIP"])
opzipcodes = food_data.index.intersection(only_pests.index)
pest_zips = (food_data.loc[opzipcodes])
#print(pest_zips["PR ZIP"])
fbi_zips.to_csv('FBI_ZIPS.csv', ",")
rats_zips.to_csv('RATS_ZIPS.csv', ",")
roach_zips.to_csv('ROACH_ZIPS.csv', ",")
pest_zips.to_csv('PEST_ZIPS.csv',",")


In [16]:
#get data for extraction
import nltk
import pandas as pd
from nltk.tokenize import sent_tokenize, word_tokenize
food_data_extract = pd.read_csv('PEST_ZIPS.csv')
text = (food_data_extract["Conditions"])
text = text.str.lower()

print(text)

0         there are cockroaches seen in the dining area.
1      there was a rat running around the back of the...
2      cockroaches were present in the establishment,...
3                       saw a mouse in the center aisle.
4      customer observed a mouse walking around in th...
5      as we were eating dinner, a cockroach climbing...
6      facility has cockroaches. person in charge doe...
7              cockroaches were found in their ice chest
8      cockroach infestation, cockroaches in kitchen ...
9      cockroaches were seen on walls in dining area....
10                there are cockroaches inside facility.
11                                   cockroaches in deli
12     cook has no food handler card. various instanc...
13     cockroach in the takeout area. employee smashe...
14     salsa tasted bad, customer saw a rat run into ...
15     a pet rat was brought into the restaurant and ...
16                  found a cockroach leg in their food.
17          customer found a co

In [17]:
#tokenize, tag and chunk data
complaint_list = []
for complaint in text.items():
    complaint_list.append(str(complaint))
    sentences = nltk.sent_tokenize(str(complaint_list))
    sentences = nltk.word_tokenize(str(sentences))
    sentences = nltk.pos_tag(sentences)
    chunkGram = r"""Chunk:{<NN|NNS><IN><DT>?<NN|NNS>+|<NN|NNS><VBD><IN><PRP$>?<NN|NNS>+|<NN|NNS><VBD|VBG><VBN>?<IN><DT>\w*?<NN>+|<NNS|NN><VBP|VBD><JJ>?<IN>?<DT>?<VBG>?<IN><DT><NN|NNS>+}"""
    chunkParser = nltk.RegexpParser(chunkGram)
    chunked = chunkParser.parse(sentences)     
    for subtree in chunked.subtrees(filter=lambda t: t.label() == 'Chunk'):
            print(subtree)
             
#putting this into a table is going to take too much work for right now because it's a tree.        
#Pest_str = [" ".join(vp.leaves()) for vp in list(parsed_sent.subtrees(filter=lambda x: x.label()=='VP'))]    
    #Chunks = pd.DataFrame(subtree) 
    #Chunks.to_csv('Chunks_extraction.csv', sep=',')



(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/IN
  the/DT
  establishment/NN)
(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/IN
  the/DT
  establishment/NN)
(Chunk mouse/NN in/IN the/DT center/NN aisle.\/NN)
(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/IN
  the/DT
  establishment/NN)
(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/IN
  the/DT
  establishment/NN)
(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/I

(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/IN
  the/DT
  establishment/NN)
(Chunk time/NN of/IN the/DT year/NN)
(Chunk cockroaches/NNS in/IN kitchen/NN)
(Chunk concentration/NN around/IN grease/NN trap/NN)
(Chunk cockroaches/NNS inside/IN facility/NN)
(Chunk \'cockroaches/NNS in/IN deli\/NN)
(Chunk instances/NNS of/IN cross/NN contamination/NN)
(Chunk droppings/NNS in/IN bag/NN)
(Chunk potatoes/NNS in/IN basement/NN)
(Chunk 'temps/NNS in/IN refrigerator/NN)
(Chunk \'cockroach/NN in/IN the/DT takeout/NN area/NN)
(Chunk piece/NN of/IN paper/NN)
(Chunk hole/NN in/IN the/DT metal/NN door/NN)
(Chunk rat/NN was/VBD brought/VBN into/IN the/DT restaurant/NN)
(Chunk workers/NNS behind/IN the/DT counter/NN)
(Chunk cockroach/NN in/IN takeout/NN order/NN)
(Chunk cockroach/NN in/IN food/NN)
(Chunk food/NN from/IN restaurant/NN)
(Chunk cockroach/NN in/IN the/DT tomatoes/NNS)
(Chunk infestation/NN n

(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/IN
  the/DT
  establishment/NN)
(Chunk time/NN of/IN the/DT year/NN)
(Chunk cockroaches/NNS in/IN kitchen/NN)
(Chunk concentration/NN around/IN grease/NN trap/NN)
(Chunk cockroaches/NNS inside/IN facility/NN)
(Chunk \'cockroaches/NNS in/IN deli\/NN)
(Chunk instances/NNS of/IN cross/NN contamination/NN)
(Chunk droppings/NNS in/IN bag/NN)
(Chunk potatoes/NNS in/IN basement/NN)
(Chunk 'temps/NNS in/IN refrigerator/NN)
(Chunk \'cockroach/NN in/IN the/DT takeout/NN area/NN)
(Chunk piece/NN of/IN paper/NN)
(Chunk hole/NN in/IN the/DT metal/NN door/NN)
(Chunk rat/NN was/VBD brought/VBN into/IN the/DT restaurant/NN)
(Chunk workers/NNS behind/IN the/DT counter/NN)
(Chunk cockroach/NN in/IN takeout/NN order/NN)
(Chunk cockroach/NN in/IN food/NN)
(Chunk food/NN from/IN restaurant/NN)
(Chunk cockroach/NN in/IN the/DT tomatoes/NNS)
(Chunk infestation/NN n

(Chunk \'cockroach/NN in/IN the/DT takeout/NN area/NN)
(Chunk piece/NN of/IN paper/NN)
(Chunk hole/NN in/IN the/DT metal/NN door/NN)
(Chunk rat/NN was/VBD brought/VBN into/IN the/DT restaurant/NN)
(Chunk workers/NNS behind/IN the/DT counter/NN)
(Chunk cockroach/NN in/IN takeout/NN order/NN)
(Chunk cockroach/NN in/IN food/NN)
(Chunk food/NN from/IN restaurant/NN)
(Chunk cockroach/NN in/IN the/DT tomatoes/NNS)
(Chunk infestation/NN near/IN cook/NN line/NN)
(Chunk access/NN into/IN wall/NN)
(Chunk cockroaches/NNS in/IN the/DT women\\\/NN)
(Chunk nothing/NN in/IN plan/NN)
(Chunk
  cockroach/NN
  was/VBD
  crawling/VBG
  on/IN
  the/DT
  dining/NN
  room/NN
  table/NN)
(Chunk cockroaches/NNS on/IN the/DT front/NN counter/NN)
(Chunk legs/NN of/IN the/DT food/NN service/NN machines/NNS)
(Chunk \'cockroach/NN in/IN pasta/NN salad/NN)
(Chunk meat/NN without/IN a/DT permit/NN)
(Chunk cockroach/NN in/IN the/DT women\\\/NN)
(Chunk cockroach/NN was/VBD on/IN the/DT dining/NN table/NN)
(Chunk cockro

(Chunk rat/NN running/VBG around/IN the/DT back/NN)
(Chunk building/NN as/IN customer/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  present/JJ
  in/IN
  the/DT
  establishment/NN)
(Chunk time/NN of/IN the/DT year/NN)
(Chunk cockroaches/NNS in/IN kitchen/NN)
(Chunk concentration/NN around/IN grease/NN trap/NN)
(Chunk cockroaches/NNS inside/IN facility/NN)
(Chunk \'cockroaches/NNS in/IN deli\/NN)
(Chunk instances/NNS of/IN cross/NN contamination/NN)
(Chunk droppings/NNS in/IN bag/NN)
(Chunk potatoes/NNS in/IN basement/NN)
(Chunk 'temps/NNS in/IN refrigerator/NN)
(Chunk \'cockroach/NN in/IN the/DT takeout/NN area/NN)
(Chunk piece/NN of/IN paper/NN)
(Chunk hole/NN in/IN the/DT metal/NN door/NN)
(Chunk rat/NN was/VBD brought/VBN into/IN the/DT restaurant/NN)
(Chunk workers/NNS behind/IN the/DT counter/NN)
(Chunk cockroach/NN in/IN takeout/NN order/NN)
(Chunk cockroach/NN in/IN food/NN)
(Chunk food/NN from/IN restaurant/NN)
(Chunk cockroach/NN in/IN the/DT tomatoes/NNS)
(Chunk infestation/NN n

...

(Chunk \'presence/NN of/IN cockroaches/NNS)
(Chunk \'cockroaches/NNS in/IN establishment/NN)
(Chunk people/NNS in/IN line/NN)
(Chunk wall/NN with/IN e/NN)
(Chunk wall/NN into/IN the/DT kitchen/NN)
(Chunk cockroach/NN in/IN soup/NN)
(Chunk \'cockroaches/NNS are/VBP in/IN the/DT facility/NN)
(Chunk cockroaches/NNS in/IN kitchen/NN)
(Chunk drawers/NNS under/IN the/DT grill/NN)
(Chunk mouse/NN in/IN facility/NN)
(Chunk mouse/NN in/IN the/DT restaurant/NN)
(Chunk droppings/NNS at/IN the/DT drinking/NN fountain/NN)
(Chunk mouse/NN in/IN the/DT restaurant/NN)
(Chunk equipment/NN on/IN the/DT floor/NN)
(Chunk sanitizer/NN in/IN the/DT facility/NN)
(Chunk cockroach/NN ran/VBD across/IN the/DT table/NN)
(Chunk door/NN of/IN kitchen/NN)
(Chunk rats/NNS in/IN dumpster/NN)
(Chunk cockroaches/NNS in/IN customers/NNS)
(Chunk cockroach/NN in/IN food\/NN)
(Chunk cockroaches/NNS in/IN the/DT floor/NN sink/NN)
(Chunk \'cockroaches/NNS walked/VBD on/IN front/NN counter/NN)
(Chunk cockroaches/NNS crawling/

(Chunk bar/NN draining/VBG into/IN a/DT hole/NN)
(Chunk cockroach/NN in/IN leftovers/NNS)
(Chunk floor/NN in/IN kitchen/NN)
(Chunk wall/NN of/IN kitchen/NN)
(Chunk \'cockroaches/NNS in/IN facility/NN)
(Chunk complaint/NN for/IN harry\\\\\\/NN)
(Chunk truck/NN that/IN a/DT cockroach/NN)
(Chunk bottle/NN on/IN the/DT counter/NN)
(Chunk bag/NN of/IN sauce/NN)
(Chunk contents/NNS of/IN the/DT bag/NN)
(Chunk
  husband/NN
  asked/VBD
  for/IN
  the/DT
  managers/NNS
  information/NN)
(Chunk complaint/NN with/IN the/DT health/NN department/NN)
(Chunk complaint/NN with/IN kfc/NN)
(Chunk cockroaches/NNS in/IN facility/NN)
(Chunk business/NN from/IN owner/NN)
(Chunk cups/NNS at/IN home/NN)
(Chunk roaches/NNS are/VBP crawling/VBG on/IN the/DT spigots/NNS)
(Chunk cockroach/NN crawled/VBD across/IN the/DT table/NN)
(Chunk waiter/NN crawled/VBD across/IN the/DT floor/NN)
(Chunk strip/NN of/IN shopping/NN center/NN)
(Chunk
  \'cockroaches/NNS
  were/VBD
  observed/VBN
  in/IN
  the/DT
  establishment

(Chunk top/NN of/IN the/DT counter/NN)
(Chunk rat/NN in/IN the/DT dumpster/NN)
(Chunk cockroaches/NNS in/IN food/NN)
(Chunk soap/NN in/IN restrooms/NNS)
(Chunk cockroaches/NNS throughout/IN facility/NN)
(Chunk cockroach/NN was/VBD observed/VBN on/IN a/DT member/NN)
(Chunk cockroach/NN on/IN the/DT dining/NN room/NN)
(Chunk cockroach/NN jumped/VBD from/IN a/DT salad/NN)
(Chunk manager/NN on/IN duty/NN)
(Chunk things/NNS at/IN the/DT hooters/NNS)
(Chunk time/NN on/IN walls/NNS tables/NNS places/NNS)
(Chunk plate/NN onto/IN floor/NN)
(Chunk cockroach/NN fell/VBD into/IN chili/NN)
(Chunk chicken/NN for/IN fajitas/NNS)
(Chunk cockroaches/NNS in/IN the/DT bathroom/NN)
(Chunk cockroaches/NNS walking/VBG on/IN the/DT top/NN)
(Chunk tables/NNS for/IN buffet\/NN)
(Chunk reeks/NN of/IN mice/NNS)
(Chunk cockroaches/NNS in/IN the/DT kitchen/NN)
(Chunk 'foods/NNS in/IN the/DT walk-in/NN)
(Chunk dishes/NNS on/IN the/DT floor/NN)
(Chunk dogs/NNS in/IN the/DT office/NN)
(Chunk board/NN of/IN health/NN 

(Chunk cockroaches/NNS in/IN kitchen/NN)
(Chunk drawers/NNS under/IN the/DT grill/NN)
(Chunk mouse/NN in/IN facility/NN)
(Chunk mouse/NN in/IN the/DT restaurant/NN)
(Chunk droppings/NNS at/IN the/DT drinking/NN fountain/NN)
(Chunk mouse/NN in/IN the/DT restaurant/NN)
(Chunk equipment/NN on/IN the/DT floor/NN)
(Chunk sanitizer/NN in/IN the/DT facility/NN)
(Chunk cockroach/NN ran/VBD across/IN the/DT table/NN)
(Chunk door/NN of/IN kitchen/NN)
(Chunk rats/NNS in/IN dumpster/NN)
(Chunk cockroaches/NNS in/IN customers/NNS)
(Chunk cockroach/NN in/IN food\/NN)
(Chunk cockroaches/NNS in/IN the/DT floor/NN sink/NN)
(Chunk \'cockroaches/NNS walked/VBD on/IN front/NN counter/NN)
(Chunk cockroaches/NNS crawling/VBG on/IN the/DT wall/NN)
(Chunk cockroaches/NNS running/VBG around/IN the/DT soda/NN)
(Chunk permit/NN in/IN system/NN)
(Chunk cockroaches/NNS in/IN store\/NN)
(Chunk \'ants/NNS on/IN the/DT soda/NN machines/NNS)
(Chunk cockroaches/NNS in/IN the/DT kitchen/NN)
(Chunk \'cockroaches/NNS in/I

(Chunk rat/NN in/IN the/DT dumpster/NN)
(Chunk cockroaches/NNS in/IN food/NN)
(Chunk soap/NN in/IN restrooms/NNS)
(Chunk cockroaches/NNS throughout/IN facility/NN)
(Chunk cockroach/NN was/VBD observed/VBN on/IN a/DT member/NN)
(Chunk cockroach/NN on/IN the/DT dining/NN room/NN)
(Chunk cockroach/NN jumped/VBD from/IN a/DT salad/NN)
(Chunk manager/NN on/IN duty/NN)
(Chunk things/NNS at/IN the/DT hooters/NNS)
(Chunk time/NN on/IN walls/NNS tables/NNS places/NNS)
(Chunk plate/NN onto/IN floor/NN)
(Chunk cockroach/NN fell/VBD into/IN chili/NN)
(Chunk chicken/NN for/IN fajitas/NNS)
(Chunk cockroaches/NNS in/IN the/DT bathroom/NN)
(Chunk cockroaches/NNS walking/VBG on/IN the/DT top/NN)
(Chunk tables/NNS for/IN buffet\/NN)
(Chunk reeks/NN of/IN mice/NNS)
(Chunk cockroaches/NNS in/IN the/DT kitchen/NN)
(Chunk 'foods/NNS in/IN the/DT walk-in/NN)
(Chunk dishes/NNS on/IN the/DT floor/NN)
(Chunk dogs/NNS in/IN the/DT office/NN)
(Chunk board/NN of/IN health/NN cant/NN)
(Chunk terry/NN was/VBD smokin